## Strategy debugging example

Debugging a strategy can be time-consuming. FreqTrade offers helper functions to visualize raw data.

## Setup

In [1]:
# Reloads local code changes
try:
    %load_ext autoreload
    %autoreload 2
except:
    %reload_ext autoreload

In [2]:
import nest_asyncio

# Fix asyncio for Jupyter
nest_asyncio.apply()

In [3]:
from os import chdir
from pathlib import Path

# Change directory to project root
chdir(Path(Path.home(), 'Documents', 'Repos', 'freqtrade'))

In [4]:
from itertools import chain

from freqtrade.configuration import Configuration

# Load configuration
# Specify values for use in this script
# Edit to match your needs
config_files = [
    Path('user_data', 'user_repo', 'config.json'),
    Path(Path.home(), '.freqtrade', 'exchange-config.json')
]
# Create config object
config = Configuration.from_files(config_files)
# Create config string for use in cli commands
conf = " ".join(
    list(chain.from_iterable([['-c', str(file)] for file in config_files])))

In [5]:
import logging

from freqtrade.loggers import setup_logging

# Configure logging
logger = logging.getLogger()
setup_logging(config)
logger.setLevel(logging.INFO)
logger.info(f'conf: {conf}')
# print(json.dumps(config, indent=1))

2019-09-10 23:13:47,520 - freqtrade.loggers - INFO - Verbosity set to 1
2019-09-10 23:13:47,523 - root - INFO - conf: -c user_data/user_repo/config.json -c /Users/jonathanraviotta/.freqtrade/exchange-config.json


## Download data

In [6]:
# Download data
!freqtrade {conf} download-data --timeframes 1m 5m 1d

2019-09-10 23:13:49,568 - freqtrade.loggers - INFO - Verbosity set to 0
2019-09-10 23:13:49,569 - freqtrade.configuration.configuration - INFO - Dry run is enabled
2019-09-10 23:13:49,569 - freqtrade.configuration.configuration - INFO - Using DB: "~/.freqtrade/sqlite://"
2019-09-10 23:13:49,569 - freqtrade.configuration.configuration - INFO - Using max_open_trades: 3 ...
2019-09-10 23:13:49,570 - freqtrade.configuration.configuration - INFO - Using user-data directory: user_data ...
2019-09-10 23:13:49,571 - freqtrade.configuration.configuration - INFO - Using data directory: user_data/data/binance ...
2019-09-10 23:13:49,571 - freqtrade.configuration.configuration - INFO - timeframes --timeframes: ['1m', '5m', '1d']
2019-09-10 23:13:49,571 - freqtrade.configuration.check_exchange - INFO - Checking exchange...
2019-09-10 23:13:49,571 - freqtrade.configuration.check_exchange - INFO - Exchange "binance" is officially supported by the Freqtrade development team.
2019-09-10 23:13:49,571 - 

## Backtest

In [7]:
# Run backtest
!freqtrade {conf} backtesting --timerange -200 --ticker-interval 15m --refresh-pairs-cached --export=trades

2019-09-10 23:14:14,236 - freqtrade.loggers - INFO - Verbosity set to 0
2019-09-10 23:14:14,236 - freqtrade.configuration.configuration - INFO - Dry run is enabled
2019-09-10 23:14:14,236 - freqtrade.configuration.configuration - INFO - Using DB: "~/.freqtrade/sqlite://"
2019-09-10 23:14:14,236 - freqtrade.configuration.configuration - INFO - Parameter -i/--ticker-interval detected ... Using ticker_interval: 15m ...
2019-09-10 23:14:14,236 - freqtrade.configuration.configuration - INFO - Using max_open_trades: 3 ...
2019-09-10 23:14:14,236 - freqtrade.configuration.configuration - INFO - Parameter --timerange detected: -200 ...
2019-09-10 23:14:14,237 - freqtrade.configuration.configuration - INFO - Using user-data directory: user_data ...
2019-09-10 23:14:14,237 - freqtrade.configuration.configuration - INFO - Using data directory: user_data/data/binance ...
2019-09-10 23:14:14,237 - freqtrade.configuration.configuration - INFO - Parameter -r/--refresh-pairs-cached detected ...
2019-0

## Plot

In [8]:
from pathlib import Path

from freqtrade.data.btanalysis import load_trades
from freqtrade.data.history import load_pair_history
from freqtrade.plot.plotting import (extract_trades_of_period,
                                     generate_candlestick_graph)
from freqtrade.resolvers import StrategyResolver

# Specify pair to plot
pair = "ETH/BTC"
# Load ticker history
tickers = load_pair_history(datadir=Path(config['datadir']),
                            ticker_interval=config['ticker_interval'],
                            pair=pair)

# Load strategy
strategy = StrategyResolver({
    'user_data_dir': Path(config['user_data_dir']),
    'strategy_path': Path(config['strategy_path'])
}).strategy

# Generate buy/sell signals using strategy
data = strategy.analyze_ticker(tickers, {'pair': pair})

# Collect trades
trades = load_trades(
    config['trade_source'],
    db_url=config.get('db_url'),
    exportfilename=config.get('exportfilename'),
)

trades = trades.loc[trades['pair'] == pair]
trades = extract_trades_of_period(data, trades)

# Build and display plot
fig = generate_candlestick_graph(pair=pair,
                                 data=data,
                                 trades=trades,
                                 indicators1=config["indicators1"],
                                 indicators2=config["indicators2"])

fig.show()

2019-09-10 23:14:17,633 - freqtrade.data.converter - INFO - Missing data fillup for ETH/BTC: before: 3330 - after: 3362
2019-09-10 23:14:17,766 - freqtrade.resolvers.iresolver - INFO - Using resolved strategy DefaultStrategy from '/Users/jonathanraviotta/Documents/Repos/freqtrade/freqtrade/strategy/default_strategy.py'...
2019-09-10 23:14:17,767 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using minimal_roi: {'40': 0.0, '30': 0.01, '20': 0.02, '0': 0.04}
2019-09-10 23:14:17,773 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using ticker_interval: 5m
2019-09-10 23:14:17,775 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using stoploss: -0.1
2019-09-10 23:14:17,777 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using trailing_stop: False
2019-09-10 23:14:17,779 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using trailing_stop_positive_offset: 0.0
2019-09-10 23:14:17,782 - freqtrade.resolvers.strategy_resolver - INFO - Strategy usi

Feel free to submit an issue or Pull Request enhancing this document if you would like to share ideas on how to best analyze the data.